# Requirements to collpase requirements tables Note + Making Concordances Concord - Tony Gui

In [13]:
import pandas as pd
import numpy as np
from dotenv import dotenv_values, find_dotenv
import os
import re
from data_cleaning_functions import requirements_clean, concordance_PCE_clean, \
    find_intermediate_industries, concordance_PCQ_clean, get_sales_from_make_matrix, clean_make_matrix, \
    get_demand_shock_from_shaipro_output, get_expenditure_weights_from_shapiro_outputs

from pathlib import Path
import matplotlib.pyplot as plt
import warnings
warnings.filterwarnings('ignore', category=FutureWarning, message=".*concatenation with empty or all-NA entries is deprecated.*")

script_dir = str(Path().resolve().parent)
file_path = os.path.join(script_dir) + "/" 
shapiro_file =  file_path + "Shapiro"
raw_data_path = file_path + "raw_bea_data" 


# 1. Load in Requirements Matrix 

In [4]:
requirements = pd.read_excel(os.path.join(raw_data_path, 'IxI_TR_2017_PRO_Det.xlsx'), sheet_name='2017')
requirements = requirements_clean(requirements)
requirements

2                                                  oilseed farming  \
nan                                                                  
oilseed farming                                           1.279779   
grain farming                                             0.002576   
vegetable and melon farming                               0.000224   
fruit and tree nut farming                                0.000245   
greenhouse, nursery, and floriculture production          0.000769   
...                                                            ...   
state and local government (hospitals and healt...             0.0   
state and local government (other services)               0.003345   
state and local government passenger transit               0.00012   
state and local government electric utilities             0.001782   
other state and local government enterprises              0.019398   

2                                                  grain farming  \
nan                                                                
oilseed farming                                         0.014409   
grain farming                                           1.160693   
vegetable and melon farming                             0.000785   
fruit and tree nut farming                              0.000826   
greenhouse, nursery, and floriculture production        0.002365   
...                                                          ...   
state and local government (hospitals and healt...           0.0   
state and local government (other services)             0.010249   
state and local government passenger transit            0.000219   
state and local government electric utilities           0.002826   
other state and local government enterprises            0.038022   

2                                                  vegetable and melon farming  \
nan                                                                              
oilseed farming                                                       0.004929   
grain farming                                                         0.005144   
vegetable and melon farming                                           1.037335   
fruit and tree nut farming                                            0.000647   
greenhouse, nursery, and floriculture production                      0.001809   
...                                                                        ...   
state and local government (hospitals and healt...                         0.0   
state and local government (other services)                           0.007965   
state and local government passenger transit                          0.000136   
state and local government electric utilities                         0.003922   
other state and local government enterprises                          0.033314   

2                                                  fruit and tree nut farming  \
nan                                                                             
oilseed farming                                                      0.001729   
grain farming                                                        0.004288   
vegetable and melon farming                                          0.000679   
fruit and tree nut farming                                           1.026228   
greenhouse, nursery, and floriculture production                     0.001517   
...                                                                       ...   
state and local government (hospitals and healt...                        0.0   
state and local government (other services)                          0.007278   
state and local government passenger transit                         0.000084   
state and local government electric utilities                        0.002444   
other state and local government enterprises                         0.022949   

2                                                  greenhouse, nursery, and floricu

# 2. Calculate Delta

In [5]:
requirements = requirements.T
with pd.option_context("future.no_silent_downcasting", True):
    requirements = requirements.fillna(0).infer_objects(copy=False)
delta = np.identity(len(requirements)) - np.linalg.inv(requirements)

# 2 (Making Concordances Concord) Adding Scrap, Used and secondhand goods and ROW adjustments to Delta

In [6]:
"""These 4 industries are found in the concordance table but not in the Reqirements table so I am 
adding them manually with row and column inputs of zero"""
concordance_but_not_requirments = ["Scrap", "Used and secondhand goods", "Rest of the world adjustment", "noncomparable imports"] 
delta = pd.DataFrame(delta, index=requirements.index, columns=requirements.columns)
delta = delta.reindex(index=requirements.index.append(pd.Index(concordance_but_not_requirments)).str.lower() , columns=requirements.columns.append(pd.Index(concordance_but_not_requirments)).str.lower() , fill_value=0)
delta

oilseed farming  \
oilseed farming                                      2.182305e-01   
grain farming                                        8.699834e-03   
vegetable and melon farming                          2.879852e-03   
fruit and tree nut farming                           7.340969e-04   
greenhouse, nursery, and floriculture production     3.650259e-04   
...                                                           ...   
other state and local government enterprises         7.913078e-09   
scrap                                                0.000000e+00   
used and secondhand goods                            0.000000e+00   
rest of the world adjustment                         0.000000e+00   
noncomparable imports                                0.000000e+00   

                                                  grain farming  \
oilseed farming                                    4.406835e-04   
grain farming                                      1.346781e-01   
vegetable and melon farming                        1.566776e-03   
fruit and tree nut farming                         1.550789e-03   
greenhouse, nursery, and floriculture production   7.710037e-04   
...                                                         ...   
other state and local government enterprises       4.430928e-08   
scrap                                              0.000000e+00   
used and secondhand goods                          0.000000e+00   
rest of the world adjustment                       0.000000e+00   
noncomparable imports                              0.000000e+00   

                                                  vegetable and melon farming  \
oilseed farming                                                  1.585737e-04   
grain farming                                                    6.322803e-04   
vegetable and melon farming                                      3.597787e-02   
fruit and tree nut farming                                       6.284265e-04   
greenhouse, nursery, and floriculture production                 2.774939e-04   
...                                                                       ...   
other state and local government enterprises                     3.368415e-08   
scrap                                                            0.000000e+00   
used and secondhand goods                                        0.000000e+00   
rest of the world adjustment                                     0.000000e+00   
noncomparable imports                                            0.000000e+00   

                                                  fruit and tree nut farming  \
oilseed farming                                                 1.608751e-04   
grain farming                                                   6.412868e-04   
vegetable and melon farming                                     5.720080e-04   
fruit and tree nut farming                                      2.553083e-02   
greenhouse, nursery, and floriculture production                2.815021e-04   
...                                                                      ...   
other state and local government enterprises                    5.390985e-08   
scrap                                                           0.000000e+00   
used and secondhand goods                                       0.000000e+00   
rest of the world adjustment                                    0.000000e+00   
noncomparable imports                                           0.000000e+00   

                                                  greenhouse, nursery, and floriculture production  \
oilseed farming                                                                       1.585959e-04   
grain farming                                                                         6.323431e-04   
vegetable and melon farming                                                           5.639853e-04   
fruit and tree nut farming                                                

# 2.5b Making Negative Values in Delta Zero

In [7]:
negative_count = (delta < 0).sum().sum()
x = negative_count/402**2
delta[delta < 0] = 0
negative_count_new = (delta < 0).sum().sum()
y = negative_count_new/402**2

# 2.5b Force negatives to be zero but adjust row sums to be same as before

In [8]:
# V = delta.sum(axis=0)
# P = delta[delta > 0].sum()
# delta.loc['norm'] = V/P
# last_values = delta.iloc[-1]
# delta[delta < 0] = 0
# delta = delta.iloc[:-1].div(last_values)
# delta

# Dealting with Intermediate Industries - Making Concordances Concord Section 3.3.1. - Operationalizing Industries without Products

# Step 1. Making Concordances Concord

In [9]:
use_table = pd.read_excel(os.path.join(raw_data_path, "Use_SUT_Framework_2017_DET.xlsx"), sheet_name="2017")
# peq_concordance = pd.read_excel(os.path.join(raw_data_path, "PEQBridge_2017_DET.xlsx"), sheet_name="2017")

# Returns all industries with zero PCE 
intermediate_industries = find_intermediate_industries(use_table)

# peq_concordance = concordance_PCQ_clean(peq_concordance)
# intermediate_industries = intermediate_industries[~intermediate_industries['Industry'].isin(peq_concordance['Industries'])]

intermediate_industries = intermediate_industries.iloc[:, [0]]
intermediate_industries = intermediate_industries.sort_values(by="Industry")
intermediate_industries

Industry
106               air and gas compressor manufacturing
163     aircraft engine and engine parts manufacturing
67          all other forging, stamping, and sintering
344  all other miscellaneous professional, scientif...
291                                   all other retail
..                                                 ...
81              valve and fittings other than plumbing
42   veneer, plywood, and engineered wood product m...
281  wholesale electronic markets and agents and br...
145                        wiring device manufacturing
173  wood kitchen cabinet and countertop manufacturing

[143 rows x 1 columns]

# Steps 2 - 5. Making Concordances Concord - Loop over Intermediate Industries and Remove

In [10]:
# requirements = pd.read_excel(os.path.join(raw_data_path, 'IxI_TR_2017_PRO_Det.xlsx'), sheet_name='2017')
# requirements = requirements_clean(requirements, wide=True)

# For the Loop 
big_lambda = np.eye(len(delta)) # create a big_lambda identity matrix that will become out final output
big_lambda = pd.DataFrame(big_lambda)
big_lambda = big_lambda.set_index(delta.index)
big_lambda.columns = delta.index
delta_industries = delta.index # save all the requirment table industries outside the loop 
removed = [] # stores all removed industries through the loop 

i = 0
for row in intermediate_industries.iloc[::-1].itertuples(): # looping backwards
    i += 1 
    current = row.Industry # industry we are currently removing
    # Create identity matrix for current loop iteration
    phi_i = np.eye(len(delta) - (i - 1))
    phi_i = pd.DataFrame(phi_i)
    phi_i = phi_i.set_index(delta_industries)
    phi_i.columns = delta_industries

    current_intermediate_use_table = delta.copy() # use a new intermediates use matrix each time we do this
    # Remove all the industries we've previously removed in earlier loop iterations 
    current_intermediate_use_table.drop(columns=removed, inplace=True)
    current_intermediate_use_table = current_intermediate_use_table.loc[[current]] # the row of the intermediates use table associated with the current industry  
    current_intermediate_use_table.drop(columns=[current], inplace=True) # drop the column associated with the current industry so we dont include it in our sum
    current_intermediate_use_table = current_intermediate_use_table.astype(float)
    current_industry_sum = current_intermediate_use_table.loc[current].sum() # find sum of row

    # just making sure that we aren't dividing by zero 
    if current_industry_sum != 0:
        current_intermediate_use_table = current_intermediate_use_table.astype(float)
        current_intermediate_use_table.loc[current] = current_intermediate_use_table.loc[current] / current_industry_sum


    current_intermediate_use_table = current_intermediate_use_table[sorted(current_intermediate_use_table.columns)] # sort the normazlied row alphabetically

    # remove the current industry from intermediate list
    intermediate_industries = intermediate_industries[intermediate_industries['Industry'] != current]
    # drop the current industry column from phi_i and industry indexing
    phi_i = phi_i.drop(columns=current)
    delta_industries = delta_industries.drop(current) 
    
    removed.append(current)

    # Update phi_i with the current industry sale shares
    phi_i.loc[current_intermediate_use_table.index] = current_intermediate_use_table.loc[current_intermediate_use_table.index].astype(np.float64).values
    big_lambda_old = big_lambda
    big_lambda = big_lambda @ phi_i

# Step 6. Making Concordances Concord - Converting IO matrix from sales shares to dollars

In [11]:
make_matrix = pd.read_excel(os.path.join(raw_data_path, "Supply_2017_DET.xlsx"), sheet_name="2017")
sales_vector = get_sales_from_make_matrix(make_matrix) # returns the sales for each industry

# these industries are not in the make matrix so i will add them manually with zero entries to preserve df sizes
industries_not_in_make_matrix = ["state and local government passenger transit", "state and local government electric utilities", \
                      "secondary smelting and alloying of aluminum", "federal electric utilities"]
not_in_make_matrix = pd.DataFrame({'Industries': industries_not_in_make_matrix, 'Sales': [0,0,0,0]})
sales_vector = pd.concat([sales_vector, not_in_make_matrix], ignore_index=True)
sales_vector.set_index('Industries', inplace=True)

# repeat the sales vector n times to make a sales matrix
sales_repeated = pd.DataFrame({f'{i}': sales_vector['Sales'].values for i in range(1, len(delta))})
sales_repeated.set_index(sales_vector.index, inplace=True)
sales_matrix = pd.concat([sales_vector, sales_repeated], axis=1)
sales_matrix.columns = delta.columns

# Y is IO matrix in dollars 
Y = delta * sales_matrix 
Y

oilseed farming  \
abrasive product manufacturing                             0.000173   
accommodation                                              0.191396   
accounting, tax preparation, bookkeeping, and p...         0.101899   
adhesive manufacturing                                     0.000000   
advertising, public relations, and related serv...         0.118975   
...                                                             ...   
wineries                                                   0.000234   
wired telecommunications carriers                          0.000000   
wireless telecommunications carriers (except sa...         0.038704   
wiring device manufacturing                                0.000000   
wood kitchen cabinet and countertop manufacturing          0.002063   

                                                    grain farming  \
abrasive product manufacturing                           0.000391   
accommodation                                            7.116882   
accounting, tax preparation, bookkeeping, and p...       0.220845   
adhesive manufacturing                                   0.000075   
advertising, public relations, and related serv...       0.231499   
...                                                           ...   
wineries                                                 0.001948   
wired telecommunications carriers                        0.017611   
wireless telecommunications carriers (except sa...       0.061536   
wiring device manufacturing                              0.000078   
wood kitchen cabinet and countertop manufacturing        0.004187   

                                                    vegetable and melon farming  \
abrasive product manufacturing                                         0.000304   
accommodation                                                          3.028562   
accounting, tax preparation, bookkeeping, and p...                     0.069017   
adhesive manufacturing                                                 0.000000   
advertising, public relations, and related serv...                     0.079510   
...                                                                         ...   
wineries                                                               0.001074   
wired telecommunications carriers                                      0.004495   
wireless telecommunications carriers (except sa...                     0.031261   
wiring device manufacturing                                            0.000000   
wood kitchen cabinet and countertop manufacturing                      0.002142   

                                                    fruit and tree nut farming  \
abrasive product manufacturing                                        0.000108   
accommodation                                                        10.755501   
accounting, tax preparation, bookkeeping, and p...                    0.073229   
adhesive manufacturing                                                0.000125   
advertising, public relations, and related serv...                    0.093259   
...                                                                        ...   
wineries                                                           3748.770641   
wired telecommunications carriers                                     0.007220   
wireless telecommunications carriers (except sa...                    0.017260   
wiring device manufacturing                                           0.000000   
wood kitchen cabinet and countertop manufacturing                     0.002217   

                                                    greenhouse, nursery, and floriculture production  \
abrasive product manufacturing                                                              0.000253   
accommodation                                                                               0.228335   
accounting, tax preparation, bookkeeping, and p...                          

# Step 7. Making Concordances Concord - Value Added for the Economy

In [12]:
sum_Y = Y.sum(axis=1).to_frame()
sum_Y.columns = ['Sales']
VA_pre_transformation = (sales_vector - sum_Y).sum()

VA_pre_transformation

Sales    1.946673e+07
dtype: float64

# Step 8. Making Concordances Concord - IO Matrix in USD

In [13]:
# new IO matrix in USD 
Y_tilde = big_lambda.T @ Y @ big_lambda
sales_tilde = big_lambda.T @ sales_vector

# Verifing that economy wide value added is identical to the pre-transformation level
sum_Y_tilde = Y_tilde.sum(axis=1).to_frame()
sum_Y_tilde.columns = ['Sales']
VA_post_transformation = (sales_tilde - sum_Y_tilde).sum()
VA_post_transformation

Sales    1.946579e+07
dtype: float64

In [14]:
"""Pre transformation and post transformation are not the same"""

differnece = VA_post_transformation - VA_pre_transformation
differnece

Sales   -938.752332
dtype: float64

# Step 9. Making Concordances Concord - Calculating New Delta

In [15]:
recip_sales = 1/sales_tilde
sales_tilde_repeated = pd.DataFrame({f'{i}': recip_sales['Sales'].values for i in range(1, len(delta))})
sales_tilde_repeated.set_index(recip_sales.index, inplace=True)
sales_tilde_matrix = pd.concat([recip_sales, sales_tilde_repeated], axis=1)
sales_tilde_matrix.columns = delta.columns

delta_tilde = Y_tilde * sales_tilde_matrix
delta = delta_tilde
delta

abrasive product manufacturing  \
grain farming                                                           0.001345   
vegetable and melon farming                                             0.001237   
fruit and tree nut farming                                              0.001126   
greenhouse, nursery, and floriculture production                        0.001245   
other crop farming                                                      0.001188   
...                                                                          ...   
other state and local government enterprises                            0.001137   
scrap                                                                   0.000237   
used and secondhand goods                                               0.001423   
rest of the world adjustment                                            0.000867   
noncomparable imports                                                   0.000873   

                                                  accommodation  \
grain farming                                          0.001055   
vegetable and melon farming                            0.003106   
fruit and tree nut farming                             0.001616   
greenhouse, nursery, and floriculture production       0.000836   
other crop farming                                     0.001441   
...                                                         ...   
other state and local government enterprises           0.000637   
scrap                                                  0.000157   
used and secondhand goods                              0.001650   
rest of the world adjustment                           0.001482   
noncomparable imports                                  0.002050   

                                                  accounting, tax preparation, bookkeeping, and payroll services  \
grain farming                                                                              0.003757                
vegetable and melon farming                                                                0.005549                
fruit and tree nut farming                                                                 0.006718                
greenhouse, nursery, and floriculture production                                           0.005241                
other crop farming                                                                         0.006109                
...                                                                                             ...                
other state and local government enterprises                                               0.006257                
scrap                                                                                      0.000845                
used and secondhand goods                                                                  0.005193                
rest of the world adjustment                                                               0.004251                
noncomparable imports                                                                      0.004346                

                                                  adhesive manufacturing  \
grain farming                                                   0.000586   
vegetable and melon farming                                     0.000527   
fruit and tree nut farming                                      0.000745   
greenhouse, nursery, and floriculture production                0.000951   
other crop farming                                              0.000647   
...                                                                  ...   
other state and local government enterprises                    0.000474   
scrap                                                           0.000178   
used and secondhand goods                                       0.002081   
rest of the world adjustment                                    0.000501   
noncomp

# End of Making Concordances Concord - Back to Requirements to Collapse Requirements Table

# 3. Merge Concordance with Delta

In [16]:
concordance = pd.read_excel(os.path.join(raw_data_path, "PCEBridge_2017_DET.xlsx"), sheet_name="2017")
concordance = concordance_PCE_clean(concordance)
concordance

PCE Bridge Products  \
4                                   new domestic autos   
5                                   new domestic autos   
6                                    new foreign autos   
7                                     new light trucks   
8                                           used autos   
..                                                 ...   
702  final consumption expenditures of nonprofit in...   
703  final consumption expenditures of nonprofit in...   
704  final consumption expenditures of nonprofit in...   
705  final consumption expenditures of nonprofit in...   
706  final consumption expenditures of nonprofit in...   

                                 PCE Bridge Industries  
4                             automobile manufacturing  
5                     motor vehicle body manufacturing  
6                             automobile manufacturing  
7        light truck and utility vehicle manufacturing  
8                                                scrap  
..                                                 ...  
702         museums, historical sites, zoos, and parks  
703          other amusement and recreation industries  
704                            religious organizations  
705  grantmaking, giving, and social advocacy organ...  
706  civic, social, professional, and similar organ...  

[703 rows x 2 columns]

In [17]:
"""the problem here is some industries in the requirments matrix still have no match to PCE they are matching to PEQ so i must drop them here when im trying to 
make the requirments table in terms of products however im not sure if this changes some of the math performed to the requirments matrix ie delta later on
"""
industries_in_requirments = set(delta.columns)
indsutries_in_concordance = set(concordance["PCE Bridge Industries"])
industires_not_in_concordance = industries_in_requirments - indsutries_in_concordance
delta = delta.drop(index=industires_not_in_concordance, columns=industires_not_in_concordance, errors='ignore')
delta

abrasive product manufacturing  \
grain farming                                                           0.001345   
vegetable and melon farming                                             0.001237   
fruit and tree nut farming                                              0.001126   
greenhouse, nursery, and floriculture production                        0.001245   
other crop farming                                                      0.001188   
...                                                                          ...   
other state and local government enterprises                            0.001137   
scrap                                                                   0.000237   
used and secondhand goods                                               0.001423   
rest of the world adjustment                                            0.000867   
noncomparable imports                                                   0.000873   

                                                  accommodation  \
grain farming                                          0.001055   
vegetable and melon farming                            0.003106   
fruit and tree nut farming                             0.001616   
greenhouse, nursery, and floriculture production       0.000836   
other crop farming                                     0.001441   
...                                                         ...   
other state and local government enterprises           0.000637   
scrap                                                  0.000157   
used and secondhand goods                              0.001650   
rest of the world adjustment                           0.001482   
noncomparable imports                                  0.002050   

                                                  accounting, tax preparation, bookkeeping, and payroll services  \
grain farming                                                                              0.003757                
vegetable and melon farming                                                                0.005549                
fruit and tree nut farming                                                                 0.006718                
greenhouse, nursery, and floriculture production                                           0.005241                
other crop farming                                                                         0.006109                
...                                                                                             ...                
other state and local government enterprises                                               0.006257                
scrap                                                                                      0.000845                
used and secondhand goods                                                                  0.005193                
rest of the world adjustment                                                               0.004251                
noncomparable imports                                                                      0.004346                

                                                  adhesive manufacturing  \
grain farming                                                   0.000586   
vegetable and melon farming                                     0.000527   
fruit and tree nut farming                                      0.000745   
greenhouse, nursery, and floriculture production                0.000951   
other crop farming                                              0.000647   
...                                                                  ...   
other state and local government enterprises                    0.000474   
scrap                                                           0.000178   
used and secondhand goods                                       0.002081   
rest of the world adjustment                                    0.000501   
noncomp

In [18]:
in_num_products = concordance['PCE Bridge Industries'].value_counts()

delta_product_columns = pd.DataFrame(index=delta.index, columns=concordance['PCE Bridge Products'])

for column in delta_product_columns: 
    industry = concordance.loc[concordance['PCE Bridge Products'] == column, 'PCE Bridge Industries'].values
    delta_product_columns[column] = delta[industry] / in_num_products[industry]

delta_product_cr = pd.DataFrame(columns=delta_product_columns.columns)
lst_for_industry = []
for row in delta_product_columns.index:
    final_value = delta_product_columns.loc[row] / in_num_products[row]
    products = concordance[concordance['PCE Bridge Industries'] == row]['PCE Bridge Products'].tolist()
    for product in products: 
        lst_for_industry.append(row)
        final_value_row = pd.DataFrame(final_value).T
        final_value_row.index = [product]
        
        delta_product_cr = pd.concat([delta_product_cr, final_value_row])

industry = pd.DataFrame(lst_for_industry, columns=['industry'])
industry.index = delta_product_cr.index
delta_product_cr = pd.concat([delta_product_cr, industry], axis = 1)
delta_product_cr

new domestic autos  \
cereals                                                       0.000095   
processed fruits and vegetables                               0.000095   
pets and related products                                     0.000095   
food furnished to employees (including military)              0.000095   
vegetables (fresh)                                            0.000058   
...                                                                ...   
less: expenditures in the united states by nonr...            0.000054   
government employees' expenditures abroad                     0.000030   
private employees' expenditures abroad                        0.000030   
u.s. travel outside the united states                         0.000030   
u.s. student expenditures                                     0.000030   

                                                    new domestic autos  \
cereals                                                       0.000034   
processed fruits and vegetables                               0.000034   
pets and related products                                     0.000034   
food furnished to employees (including military)              0.000034   
vegetables (fresh)                                            0.000042   
...                                                                ...   
less: expenditures in the united states by nonr...            0.000065   
government employees' expenditures abroad                     0.000034   
private employees' expenditures abroad                        0.000034   
u.s. travel outside the united states                         0.000034   
u.s. student expenditures                                     0.000034   

                                                    new foreign autos  \
cereals                                                      0.000095   
processed fruits and vegetables                              0.000095   
pets and related products                                    0.000095   
food furnished to employees (including military)             0.000095   
vegetables (fresh)                                           0.000058   
...                                                               ...   
less: expenditures in the united states by nonr...           0.000054   
government employees' expenditures abroad                    0.000030   
private employees' expenditures abroad                       0.000030   
u.s. travel outside the united states                        0.000030   
u.s. student expenditures                                    0.000030   

                                                    new light trucks  \
cereals                                                     0.000142   
processed fruits and vegetables                             0.000142   
pets and related products                                   0.000142   
food furnished to employees (including military)            0.000142   
vegetables (fresh)                                          0.000286   
...                                                              ...   
less: expenditures in the united states by nonr...          0.000535   
government employees' expenditures abroad                   0.000324   
private employees' expenditures abroad                      0.000324   
u.s. travel outside the united states                       0.000324   
u.s. student expenditures                                   0.000324   

                                                      used autos  \
cereals                                             5.387641e-07   
processed fruits and vegetables                     5.387641e-07   
pets and related products                           5.387641e-07   
food furnished to employees (including military)    5.387641e-07   
vegetables (fresh)                                  1.088359e-06   
...                                                          ...   
less: expenditures in the united states by nonr...  1.39

# 4. Collapse columns

In [19]:
delta_products = delta_product_cr.T.groupby(delta_product_cr.columns).sum().T
delta_products

accessories and parts  \
cereals                                                         0.002788   
processed fruits and vegetables                                 0.002788   
pets and related products                                       0.002788   
food furnished to employees (including military)                0.002788   
vegetables (fresh)                                               0.00315   
...                                                                  ...   
less: expenditures in the united states by nonr...               0.00433   
government employees' expenditures abroad                       0.002627   
private employees' expenditures abroad                          0.002627   
u.s. travel outside the united states                           0.002627   
u.s. student expenditures                                       0.002627   

                                                   air transportation  \
cereals                                                      0.000218   
processed fruits and vegetables                              0.000218   
pets and related products                                    0.000218   
food furnished to employees (including military)             0.000218   
vegetables (fresh)                                           0.000333   
...                                                               ...   
less: expenditures in the united states by nonr...           0.000284   
government employees' expenditures abroad                     0.00023   
private employees' expenditures abroad                        0.00023   
u.s. travel outside the united states                         0.00023   
u.s. student expenditures                                     0.00023   

                                                   alcohol in purchased meals  \
cereals                                                              0.001629   
processed fruits and vegetables                                      0.001629   
pets and related products                                            0.001629   
food furnished to employees (including military)                     0.001629   
vegetables (fresh)                                                   0.001638   
...                                                                       ...   
less: expenditures in the united states by nonr...                   0.001605   
government employees' expenditures abroad                            0.000982   
private employees' expenditures abroad                               0.000982   
u.s. travel outside the united states                                0.000982   
u.s. student expenditures                                            0.000982   

                                                   all other professional medical services  \
cereals                                                                           0.000074   
processed fruits and vegetables                                                   0.000074   
pets and related products                                                         0.000074   
food furnished to employees (including military)                                  0.000074   
vegetables (fresh)                                                                0.000159   
...                                                                                    ...   
less: expenditures in the united states by nonr...                                0.000258   
government employees' expenditures abroad                                         0.000137   
private employees' expenditures abroad                                            0.000137   
u.s. travel outside the united states                                             0.000137   
u.s. student expenditures                                                         0.000137   

                                                   amusement parks, campgrounds, and related recreational services  \
cereals                                  

# 5. Make Matrix to Sales

In [20]:
make_matrix = pd.read_excel(os.path.join(raw_data_path, "Supply_2017_DET.xlsx"), sheet_name='2017')
sales = get_sales_from_make_matrix(make_matrix)
sales

3                                          Industries   Sales
0                                     oilseed farming   37922
1                                       grain farming   66790
2                         vegetable and melon farming   18582
3                          fruit and tree nut farming   29731
4    greenhouse, nursery, and floriculture production   19868
..                                                ...     ...
397      other state and local government enterprises  107059
398                                             scrap   10763
399                         used and secondhand goods       0
400                             noncomparable imports       0
401                      rest of the world adjustment    3468

[402 rows x 2 columns]

# 6. Merge concordance with sales 

In [21]:
product_sales = pd.merge(concordance, sales, left_on='PCE Bridge Industries', right_on='Industries')
product_sales = product_sales[["PCE Bridge Products", "Industries", 'Sales']]
product_sales

PCE Bridge Products  \
0                                   new domestic autos   
1                                   new domestic autos   
2                                    new foreign autos   
3                                     new light trucks   
4                                           used autos   
..                                                 ...   
698  final consumption expenditures of nonprofit in...   
699  final consumption expenditures of nonprofit in...   
700  final consumption expenditures of nonprofit in...   
701  final consumption expenditures of nonprofit in...   
702  final consumption expenditures of nonprofit in...   

                                            Industries   Sales  
0                             automobile manufacturing   32758  
1                     motor vehicle body manufacturing   10556  
2                             automobile manufacturing   32758  
3        light truck and utility vehicle manufacturing  215421  
4                                                scrap   10763  
..                                                 ...     ...  
698         museums, historical sites, zoos, and parks   20894  
699          other amusement and recreation industries   81734  
700                            religious organizations  100202  
701  grantmaking, giving, and social advocacy organ...   58458  
702  civic, social, professional, and similar organ...   95191  

[703 rows x 3 columns]

# 7. Group sum of Sales for every Product

In [22]:
# calculates the number of product categories an Industry belongs to 
product_sales['In#Products'] = product_sales['Industries'].map(product_sales['Industries'].value_counts())
product_sales["Ratio_in_Product"] = product_sales['Sales'] / product_sales['In#Products'] 
product_sales['Sales_Sum'] = product_sales.groupby('PCE Bridge Products')['Ratio_in_Product'].transform('sum')
product_sales

PCE Bridge Products  \
0                                   new domestic autos   
1                                   new domestic autos   
2                                    new foreign autos   
3                                     new light trucks   
4                                           used autos   
..                                                 ...   
698  final consumption expenditures of nonprofit in...   
699  final consumption expenditures of nonprofit in...   
700  final consumption expenditures of nonprofit in...   
701  final consumption expenditures of nonprofit in...   
702  final consumption expenditures of nonprofit in...   

                                            Industries   Sales  In#Products  \
0                             automobile manufacturing   32758            2   
1                     motor vehicle body manufacturing   10556            1   
2                             automobile manufacturing   32758            2   
3        light truck and utility vehicle manufacturing  215421            1   
4                                                scrap   10763            6   
..                                                 ...     ...          ...   
698         museums, historical sites, zoos, and parks   20894            3   
699          other amusement and recreation industries   81734            3   
700                            religious organizations  100202            2   
701  grantmaking, giving, and social advocacy organ...   58458            3   
702  civic, social, professional, and similar organ...   95191            4   

     Ratio_in_Product     Sales_Sum  
0        16379.000000  2.693500e+04  
1        10556.000000  2.693500e+04  
2        16379.000000  1.637900e+04  
3       215421.000000  2.154210e+05  
4         1793.833333  1.793833e+03  
..                ...           ...  
698       6964.666667  1.554667e+06  
699      27244.666667  1.554667e+06  
700      50101.000000  1.554667e+06  
701      19486.000000  1.554667e+06  
702      23797.750000  1.554667e+06  

[703 rows x 6 columns]

# 8. Sales Share 

In [23]:
product_sales['Sale Share'] = product_sales["Ratio_in_Product"] / product_sales["Sales_Sum"]
product_sales = product_sales.rename(columns={'Industries': 'industry'})
product_sales = product_sales.rename(columns={'PCE Bridge Products': 'product'})
product_sales

product  \
0                                   new domestic autos   
1                                   new domestic autos   
2                                    new foreign autos   
3                                     new light trucks   
4                                           used autos   
..                                                 ...   
698  final consumption expenditures of nonprofit in...   
699  final consumption expenditures of nonprofit in...   
700  final consumption expenditures of nonprofit in...   
701  final consumption expenditures of nonprofit in...   
702  final consumption expenditures of nonprofit in...   

                                              industry   Sales  In#Products  \
0                             automobile manufacturing   32758            2   
1                     motor vehicle body manufacturing   10556            1   
2                             automobile manufacturing   32758            2   
3        light truck and utility vehicle manufacturing  215421            1   
4                                                scrap   10763            6   
..                                                 ...     ...          ...   
698         museums, historical sites, zoos, and parks   20894            3   
699          other amusement and recreation industries   81734            3   
700                            religious organizations  100202            2   
701  grantmaking, giving, and social advocacy organ...   58458            3   
702  civic, social, professional, and similar organ...   95191            4   

     Ratio_in_Product     Sales_Sum  Sale Share  
0        16379.000000  2.693500e+04    0.608094  
1        10556.000000  2.693500e+04    0.391906  
2        16379.000000  1.637900e+04    1.000000  
3       215421.000000  2.154210e+05    1.000000  
4         1793.833333  1.793833e+03    1.000000  
..                ...           ...         ...  
698       6964.666667  1.554667e+06    0.004480  
699      27244.666667  1.554667e+06    0.017524  
700      50101.000000  1.554667e+06    0.032226  
701      19486.000000  1.554667e+06    0.012534  
702      23797.750000  1.554667e+06    0.015307  

[703 rows x 7 columns]

# 9. Merge Sale shares and Delta

In [24]:
df_reset = delta_products.reset_index()
delta_products = df_reset.rename(columns={'index': 'product'})
delta_products_saleshare = delta_products.merge(product_sales, how = 'inner', on = ['industry', 'product'])
delta_products_saleshare = delta_products_saleshare.drop(columns=['Sales_Sum', "Ratio_in_Product", "In#Products", "Sales", "industry"])
delta_products_saleshare = delta_products_saleshare.set_index(delta_products_saleshare.columns[0])
delta_products_saleshare

accessories and parts  \
product                                                                    
cereals                                                         0.002788   
processed fruits and vegetables                                 0.002788   
pets and related products                                       0.002788   
food furnished to employees (including military)                0.002788   
vegetables (fresh)                                               0.00315   
...                                                                  ...   
less: expenditures in the united states by nonr...               0.00433   
government employees' expenditures abroad                       0.002627   
private employees' expenditures abroad                          0.002627   
u.s. travel outside the united states                           0.002627   
u.s. student expenditures                                       0.002627   

                                                   air transportation  \
product                                                                 
cereals                                                      0.000218   
processed fruits and vegetables                              0.000218   
pets and related products                                    0.000218   
food furnished to employees (including military)             0.000218   
vegetables (fresh)                                           0.000333   
...                                                               ...   
less: expenditures in the united states by nonr...           0.000284   
government employees' expenditures abroad                     0.00023   
private employees' expenditures abroad                        0.00023   
u.s. travel outside the united states                         0.00023   
u.s. student expenditures                                     0.00023   

                                                   alcohol in purchased meals  \
product                                                                         
cereals                                                              0.001629   
processed fruits and vegetables                                      0.001629   
pets and related products                                            0.001629   
food furnished to employees (including military)                     0.001629   
vegetables (fresh)                                                   0.001638   
...                                                                       ...   
less: expenditures in the united states by nonr...                   0.001605   
government employees' expenditures abroad                            0.000982   
private employees' expenditures abroad                               0.000982   
u.s. travel outside the united states                                0.000982   
u.s. student expenditures                                            0.000982   

                                                   all other professional medical services  \
product                                                                                      
cereals                                                                           0.000074   
processed fruits and vegetables                                                   0.000074   
pets and related products                                                         0.000074   
food furnished to employees (including military)                                  0.000074   
vegetables (fresh)                                                                0.000159   
...                                                                                    ...   
less: expenditures in the united states by nonr...                                0.000258   
government employees' expenditures abroad                                         0.000137   
private employees' expenditures abroad                                            0.000137   
u.s. travel outside the 

# 10. weightTimesDeltaValue + 11.

In [25]:
# Convert from Wide to Long
delta_final = delta_products_saleshare.reset_index().melt(id_vars=[delta_products_saleshare.index.name, "Sale Share"],
                                var_name="Column Products", value_name="value")

# Just Renaming and Reordering
delta_final = delta_final.rename(columns={delta_products_saleshare.index.name: "Row Products"})
delta_final = delta_final[['Row Products', 'Column Products', 'value', 'Sale Share']]
# Calculating weightTimesDeltaValue
delta_final["weightTimesDeltaValue"] = delta_final["value"] * delta_final["Sale Share"]

# Sum weightTimesDeltaValue grouping by Row Products AND Column Products
delta_final = delta_final.groupby(['Row Products', 'Column Products']).sum()
delta_final
# Convert Back to Wide Format 
delta_final = delta_final.pivot_table(values='weightTimesDeltaValue', index='Row Products', columns='Column Products')

# Removes Index and Column Names cuz it looks better. Both Index and Columns are simply Product Categories now
delta_final.columns.name = None 
delta_final.index.name = None 
delta_final

accessories and parts  \
accessories and parts                                            0.09814   
air transportation                                                0.0008   
alcohol in purchased meals                                      0.001887   
all other professional medical services                          0.00156   
amusement parks, campgrounds, and related recre...              0.003495   
...                                                                  ...   
water transportation                                            0.003765   
window coverings                                                0.004972   
wine                                                            0.015942   
women's and girls' clothing                                      0.00221   
workers' compensation                                           0.000579   

                                                   air transportation  \
accessories and parts                                          0.0005   
air transportation                                           0.000064   
alcohol in purchased meals                                   0.000156   
all other professional medical services                      0.000133   
amusement parks, campgrounds, and related recre...           0.000277   
...                                                               ...   
water transportation                                         0.000403   
window coverings                                              0.00017   
wine                                                         0.000451   
women's and girls' clothing                                  0.000098   
workers' compensation                                        0.000138   

                                                   alcohol in purchased meals  \
accessories and parts                                                0.003793   
air transportation                                                   0.001081   
alcohol in purchased meals                                            0.00172   
all other professional medical services                              0.002704   
amusement parks, campgrounds, and related recre...                   0.001731   
...                                                                       ...   
water transportation                                                 0.001152   
window coverings                                                     0.001086   
wine                                                                 0.002823   
women's and girls' clothing                                          0.000651   
workers' compensation                                                 0.00066   

                                                   all other professional medical services  \
accessories and parts                                                              0.00046   
air transportation                                                                 0.00005   
alcohol in purchased meals                                                        0.000082   
all other professional medical services                                           0.000216   
amusement parks, campgrounds, and related recre...                                0.000159   
...                                                                                    ...   
water transportation                                                              0.000122   
window coverings                                                                  0.000115   
wine                                                                               0.00039   
women's and girls' clothing                                                       0.000082   
workers' compensation                                                             0.000118   

                                                   amusement parks, campgrounds, and related recreational services  \
accessories and parts                    

# 12. Calculate Gamma

In [26]:
row_sums = delta_final.sum(axis=1)
gamma = pd.DataFrame(row_sums, columns=['Row_Sum'])
gamma.index = delta_final.index 
gamma

Row_Sum
accessories and parts                               0.504767
air transportation                                  0.066446
alcohol in purchased meals                          0.155212
all other professional medical services             0.101536
amusement parks, campgrounds, and related recre...  0.151167
...                                                      ...
water transportation                                0.151609
window coverings                                    0.130697
wine                                                0.539424
women's and girls' clothing                            0.078
workers' compensation                               0.076973

[212 rows x 1 columns]

# 13. Calculate Omega

In [27]:
delta_gamma = delta_final.merge(gamma, left_on=gamma.index, right_on=delta_final.index)
delta_gamma = delta_gamma.set_index(delta_gamma.columns[0])
row_sums = delta_gamma.iloc[:, -1]
row_sums[row_sums == 0] = np.nan
omega = delta_gamma.iloc[:, :-1].div(row_sums, axis=0)
omega.columns.name = None 
omega.index.name = None 
omega

accessories and parts  \
accessories and parts                                           0.194427   
air transportation                                              0.012047   
alcohol in purchased meals                                      0.012157   
all other professional medical services                         0.015368   
amusement parks, campgrounds, and related recre...              0.023122   
...                                                                  ...   
water transportation                                            0.024831   
window coverings                                                0.038041   
wine                                                            0.029554   
women's and girls' clothing                                     0.028334   
workers' compensation                                           0.007523   

                                                   air transportation  \
accessories and parts                                         0.00099   
air transportation                                           0.000962   
alcohol in purchased meals                                   0.001004   
all other professional medical services                      0.001307   
amusement parks, campgrounds, and related recre...           0.001835   
...                                                               ...   
water transportation                                         0.002661   
window coverings                                               0.0013   
wine                                                         0.000837   
women's and girls' clothing                                  0.001254   
workers' compensation                                        0.001788   

                                                   alcohol in purchased meals  \
accessories and parts                                                0.007515   
air transportation                                                   0.016267   
alcohol in purchased meals                                           0.011078   
all other professional medical services                              0.026634   
amusement parks, campgrounds, and related recre...                   0.011453   
...                                                                       ...   
water transportation                                                 0.007599   
window coverings                                                     0.008308   
wine                                                                 0.005234   
women's and girls' clothing                                          0.008341   
workers' compensation                                                0.008571   

                                                   all other professional medical services  \
accessories and parts                                                              0.00091   
air transportation                                                                0.000754   
alcohol in purchased meals                                                        0.000525   
all other professional medical services                                           0.002126   
amusement parks, campgrounds, and related recre...                                0.001055   
...                                                                                    ...   
water transportation                                                              0.000803   
window coverings                                                                  0.000882   
wine                                                                              0.000724   
women's and girls' clothing                                                       0.001052   
workers' compensation                                                             0.001535   

                                                   amusement parks, campgrounds, and related recreational services  \
accessories and parts                    

# Start of Doing our Supply/demand contribution graph properly (Which influenceer has hte most influence?)

In [3]:
shapiro_code_output = pd.read_excel(os.path.join(shapiro_file, 'shaprio_stata_output_excel.xlsx'))
shapiro_code_output

time_month       pce      core  pce_spend  core_goods  core_serv  \
0   1969-01-01  0.003912  0.003770     583479    0.002418   0.004709   
1   1969-02-01  0.002544  0.003443     588675    0.003164   0.003553   
2   1969-03-01  0.004697  0.004679     588862    0.004147   0.005047   
3   1969-04-01  0.004406  0.003829     593870    0.003163   0.004273   
4   1969-05-01  0.004012  0.004021     600271    0.001818   0.005449   
..         ...       ...       ...        ...         ...        ...   
665 2024-06-01  0.001177  0.002217   19747490    0.001005   0.002610   
666 2024-07-01  0.001581  0.001633   19859264   -0.000995   0.002493   
667 2024-08-01  0.001165  0.001581   19898041   -0.001743   0.002667   
668 2024-09-01  0.001803  0.002612   20027196    0.001081   0.003105   
669 2024-10-01  0.002380  0.002727   20099540    0.000046   0.003600   

     core_goods_spend  core_serv_spend      util        IP  ...  \
0              180917           272374  0.002323  0.006049  ...   
1              182558           274872  0.002785  0.006400  ...   
2              181078           276007  0.004230  0.007840  ...   
3              183191           279048 -0.007235 -0.003679  ...   
4              183901           282744 -0.007325 -0.003778  ...   
..                ...              ...       ...       ...  ...   
665           4298479         13213608  0.001977  0.002885  ...   
666           4335381         13277465 -0.008112 -0.007153  ...   
667           4311876         13352011  0.003898  0.004943  ...   
668           4372800         13418556 -0.005910 -0.004806  ...   
669           4373608         13495929 -0.003793 -0.002625  ...   

     demN_contr_m_na  supP_contr_m_na  supN_contr_m_na  amb_contr_m_na  \
0           0.000371         0.000196         0.002849             0.0   
1          -0.000103         0.000528         0.001292             0.0   
2           0.000833         0.000370         0.002790             0.0   
3           0.000533         0.000642         0.002478             0.0   
4           0.000387         0.000119         0.003007             0.0   
..               ...              ...              ...             ...   
665        -0.000562        -0.000719         0.001130             0.0   
666        -0.000063        -0.000622         0.001565             0.0   
667        -0.000167        -0.000580         0.001404             0.0   
668         0.000510        -0.001446         0.001196             0.0   
669        -0.000131        -0.000676         0.002405             0.0   

     dem_inf_y  sup_inf_y  dem_inf_m_na  sup_inf_m_na     time  zero  
0          NaN        NaN      0.271792      0.451262   1969m1     0  
1          NaN        NaN      0.188780      0.289968   1969m2     0  
2          NaN        NaN      0.347811      0.569921   1969m3     0  
3          NaN        NaN      0.382890      0.473471   1969m4     0  
4          NaN        NaN      0.296997      0.453351   1969m5     0  
..         ...        ...           ...           ...      ...   ...  
665   2.763617   2.241206      0.161921      0.078397   2024m6     0  
666   2.837753   2.243578      0.219982      0.134001   2024m7     0  
667   2.486539   2.153146      0.102052      0.124801   2024m8     0  
668   2.553403   1.723337      0.391839     -0.053052   2024m9     0  
669   2.895713   1.773465      0.241637      0.241469  2024m10     0  

[670 rows x 1145 columns]

In [4]:
haver_code_concordance = pd.read_excel(os.path.join(shapiro_file, 'Haver Codes to Product Names.xlsx'))
mapping = dict(zip(haver_code_concordance['Shapiro Price Name'], haver_code_concordance['PCE Category']))
""" I dont know why but in Shapiro's output the expenditure for water transport is titled s"""
mapping["s"] = "Water transportation (65)"

In [ ]:
expenditure_weights = get_expenditure_weights_from_shapiro_outputs(shapiro_code_output, mapping)
expenditure_weights

C:\Users\TonyGui\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\pandas\core\indexes\base.py:7631: FutureWarning: Dtype inference on a pandas object (Series, Index, ExtensionArray) is deprecated. The Index constructor will keep the original dtype in the future. Call `infer_objects` on the result to get the old behavior.
  return Index(index_like, name=name, copy=copy)


time_month                                         1969-01-01 1969-02-01  \
Water transportation (65)                            0.000007   0.000007   
                Pleasure boats, aircraft, and o...   0.003254   0.003321   
            Educational books (96)                   0.000911   0.000944   
                Dishes and flatware                  0.002522   0.002545   
                Nonelectric cookware and tableware   0.003422   0.003433   
...                                                       ...        ...   
                Motor vehicle maintenance and r...   0.016538   0.016492   
                Net motor vehicle and other tra...   0.006067   0.006055   
                Foreign travel by U.S. resident...   0.007118    0.00744   
                Less: Expenditures in the Unite...  -0.003715  -0.003789   
NaN                                                  0.015525   0.015432   

time_month                                         1969-03-01 1969-04-01  \
Water transportation (65)                            0.000007   0.000008   
                Pleasure boats, aircraft, and o...   0.003552   0.003405   
            Educational books (96)                   0.000948   0.000946   
                Dishes and flatware                  0.002555   0.002569   
                Nonelectric cookware and tableware   0.003423   0.003422   
...                                                       ...        ...   
                Motor vehicle maintenance and r...   0.016481   0.016602   
                Net motor vehicle and other tra...    0.00603   0.006091   
                Foreign travel by U.S. resident...   0.007761   0.007993   
                Less: Expenditures in the Unite...  -0.003899  -0.003994   
NaN                                                  0.015377   0.015498   

time_month                                         1969-05-01 1969-06-01  \
Water transportation (65)                            0.000008   0.000008   
                Pleasure boats, aircraft, and o...   0.003723   0.003635   
            Educational books (96)                    0.00097    0.00096   
                Dishes and flatware                   0.00259   0.002546   
                Nonelectric cookware and tableware   0.003425   0.003345   
...                                                       ...        ...   
                Motor vehicle maintenance and r...     0.0166   0.016558   
                Net motor vehicle and other tra...   0.006075   0.006034   
                Foreign travel by U.S. resident...   0.007855   0.007742   
                Less: Expenditures in the Unite...  -0.003935  -0.003893   
NaN                                                  0.015515   0.015431   

time_month                                         1969-07-01 1969-08-01  \
Water transportation (65)                            0.000008   0.000008   
                Pleasure boats, aircraft, and o...   0.003655    0.00344   
            Educational books (96)                   0.000977   0.000972   
                Dishes and flatware                  0.002521   0.002529   
                Nonelectric cookware and tableware   0.003289   0.003277   
...                                                       ...        ...   
                Motor vehicle maintenance and r...   0.016694   0.016779   
                Net motor vehicle and other tra...   0.006091   0.006144   
                Foreign travel by U.S. resident...   0.007784   0.007845   
                Less: Expenditures in the Unite...  -0.003894  -0.003883   
NaN                                                  0.015574   0.015678   

time_month                                         1969-09-01 1969-10-01  ...  \
Water transportation (65)                            0.000008   0.000008  ...   
                Pleasure boats, aircraft, and o...   0.003504   0.003707  ...   
            Educational books (96)                   0.000969   0.001001  ...   
                Dishes a

In [ ]:
demand_shock = get_demand_shock_from_shaipro_output(shapiro_code_output, mapping)
demand_shock

C:\Users\TonyGui\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\pandas\core\indexes\base.py:7631: FutureWarning: Dtype inference on a pandas object (Series, Index, ExtensionArray) is deprecated. The Index constructor will keep the original dtype in the future. Call `infer_objects` on the result to get the old behavior.
  return Index(index_like, name=name, copy=copy)


In [14]:
inflation_decomped = shapiro_code_output[['time_month', "sup_inf_m", "dem_inf_m"]]
inflation_decomped

time_month  sup_inf_m  dem_inf_m
0   1969-01-01   5.551586   3.310707
1   1969-02-01   3.535655   2.289026
2   1969-03-01   7.057554   4.254511
3   1969-04-01   5.831963   4.692687
4   1969-05-01   5.577933   3.622766
..         ...        ...        ...
665 2024-06-01   0.944828   1.960445
666 2024-07-01   1.619912   2.671962
667 2024-08-01   1.507933   1.231524
668 2024-09-01  -0.634769   4.804743
669 2024-10-01   2.936427   2.938494

[670 rows x 3 columns]

In [ ]:
supply_inflation = inflation_decomped["sup_inf_m"]
demand_inflation =inflation_decomped["dem_inf_m"]

supply_inflation['supply_pos'] = supply_inflation['Supply Inflation'].apply(lambda x: x if x > 0 else 0)
demand_inflation['demand_pos'] = demand_inflation['Demand Inflation'].apply(lambda x: x if x > 0 else 0)
supply_inflation['supply_neg'] = supply_inflation['Supply Inflation'].apply(lambda x: x if x < 0 else 0)
demand_inflation['demand_neg'] = demand_inflation['Demand Inflation'].apply(lambda x: x if x < 0 else 0)

demand_inflation = demand_inflation.iloc[:-1]
supply_inflation = supply_inflation.iloc[:-1]

plt.figure(figsize=(26, 12))

plt.stackplot(supply_inflation.index, demand_inflation['demand_pos'], supply_inflation['supply_pos'], colors= ["#008000", "#FF0000"], labels = ["Deamnd", "Supply"])
plt.stackplot(supply_inflation.index, demand_inflation['demand_neg'], supply_inflation['supply_neg'], colors= ["#008000", "#FF0000"])
plt.xlabel('Date')
plt.ylabel('Inflation Percent')
plt.title('STEP ONE GRAPH')
plt.legend()

x = supply_inflation.index
y = CPI["Inflation"]

plt.plot(x, y)  
plt.xticks(x[::12])

In [ ]:
def graph_function_shapiro_output(CPI, expenditure_weights, Demand, inflation_df):
    demand_times_weight = np.multiply(Demand, expenditure_weights)
    demand_bar = np.multiply(demand_times_weight, inflation_df)

    one_minus_Demand = 1 - Demand
    supply_times_weight = np.multiply(one_minus_Demand, expenditure_weights)
    supply_bar = np.multiply(supply_times_weight, inflation_df)

    demand_sum = supply_bar.sum()
    supply_sum = supply_bar.sum()

    supply_inflation = pd.DataFrame(supply_sum, columns=['Supply Inflation'])
    demand_inflation = pd.DataFrame(demand_sum, columns=['Demand Inflation'])

    supply_inflation['supply_pos'] = supply_inflation['Supply Inflation'].apply(lambda x: x if x > 0 else 0)
    demand_inflation['demand_pos'] = demand_inflation['Demand Inflation'].apply(lambda x: x if x > 0 else 0)
    supply_inflation['supply_neg'] = supply_inflation['Supply Inflation'].apply(lambda x: x if x < 0 else 0)
    demand_inflation['demand_neg'] = demand_inflation['Demand Inflation'].apply(lambda x: x if x < 0 else 0)

    demand_inflation = demand_inflation.iloc[:-1]
    supply_inflation = supply_inflation.iloc[:-1]

    plt.figure(figsize=(26, 12))

    plt.stackplot(supply_inflation.index, demand_inflation['demand_pos'], supply_inflation['supply_pos'], colors= ["#008000", "#FF0000"], labels = ["Deamnd", "Supply"])
    plt.stackplot(supply_inflation.index, demand_inflation['demand_neg'], supply_inflation['supply_neg'], colors= ["#008000", "#FF0000"])
    plt.xlabel('Date')
    plt.ylabel('Inflation Percent')
    plt.title('STEP ONE GRAPH')
    plt.legend()

    x = supply_inflation.index
    y = CPI["Inflation"]

    plt.plot(x, y)  
    plt.xticks(x[::12])

    return plt


